In [31]:
# importings
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import math
%matplotlib notebook

In [3]:
#importing raw data
covid_raw = pd.read_csv('../Data/Raw/owid-covid-data.csv')

In [4]:
covid_raw.head(5)

iso_code continent     location        date  total_cases  new_cases  \
0      AFG      Asia  Afghanistan  2020-01-05          NaN        0.0   
1      AFG      Asia  Afghanistan  2020-01-06          NaN        0.0   
2      AFG      Asia  Afghanistan  2020-01-07          NaN        0.0   
3      AFG      Asia  Afghanistan  2020-01-08          NaN        0.0   
4      AFG      Asia  Afghanistan  2020-01-09          NaN        0.0   

   new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  ...  \
0                 NaN           NaN         0.0                  NaN  ...   
1                 NaN           NaN         0.0                  NaN  ...   
2                 NaN           NaN         0.0                  NaN  ...   
3                 NaN           NaN         0.0                  NaN  ...   
4                 NaN           NaN         0.0                  NaN  ...   

   male_smokers  handwashing_facilities  hospital_beds_per_thousand  \
0           NaN                  37.746                         0.5   
1           NaN                  37.746                         0.5   
2           NaN                  37.746                         0.5   
3           NaN                  37.746                         0.5   
4           NaN                  37.746                         0.5   

   life_expectancy  human_development_index  population  \
0            64.83                    0.511  41128772.0   
1            64.83                    0.511  41128772.0   
2            64.83                    0.511  41128772.0   
3            64.83                    0.511  41128772.0   
4            64.83                    0.511  41128772.0   

   excess_mortality_cumulative_absolute  excess_mortality_cumulative  \
0                                   NaN                          NaN   
1                                   NaN                          NaN   
2                                   NaN                          NaN   
3                                   NaN                          NaN   
4                                   NaN                          NaN   

   excess_mortality  excess_mortality_cumulative_per_million  
0               NaN                                      NaN  
1               NaN                                      NaN  
2               NaN                                      NaN  
3               NaN                                      NaN  
4               NaN                                      NaN  

[5 rows x 67 columns]

In [5]:
print(covid_raw.columns)

Index(['iso_code', 'continent', 'location', 'date', 'total_cases', 'new_cases',
       'new_cases_smoothed', 'total_deaths', 'new_deaths',
       'new_deaths_smoothed', 'total_cases_per_million',
       'new_cases_per_million', 'new_cases_smoothed_per_million',
       'total_deaths_per_million', 'new_deaths_per_million',
       'new_deaths_smoothed_per_million', 'reproduction_rate', 'icu_patients',
       'icu_patients_per_million', 'hosp_patients',
       'hosp_patients_per_million', 'weekly_icu_admissions',
       'weekly_icu_admissions_per_million', 'weekly_hosp_admissions',
       'weekly_hosp_admissions_per_million', 'total_tests', 'new_tests',
       'total_tests_per_thousand', 'new_tests_per_thousand',
       'new_tests_smoothed', 'new_tests_smoothed_per_thousand',
       'positive_rate', 'tests_per_case', 'tests_units', 'total_vaccinations',
       'people_vaccinated', 'people_fully_vaccinated', 'total_boosters',
       'new_vaccinations', 'new_vaccinations_smoothed',
       't

In [6]:
covid_new = covid_raw.drop(['new_cases_smoothed','new_deaths_smoothed', 'total_cases_per_million',
       'new_cases_per_million', 'new_cases_smoothed_per_million',
       'total_deaths_per_million', 'new_deaths_per_million',
       'new_deaths_smoothed_per_million',
       'icu_patients_per_million',
       'hosp_patients_per_million',
       'weekly_icu_admissions_per_million',
       'weekly_hosp_admissions_per_million',
       'total_tests_per_thousand', 'new_tests_per_thousand',
       'new_tests_smoothed', 'new_tests_smoothed_per_thousand',
       'new_vaccinations_smoothed',
       'total_vaccinations_per_hundred', 'people_vaccinated_per_hundred',
       'people_fully_vaccinated_per_hundred', 'total_boosters_per_hundred',
       'new_vaccinations_smoothed_per_million',
       'new_people_vaccinated_smoothed_per_hundred','excess_mortality_cumulative_per_million'], axis=1)

In [7]:
# We want to use data's until there are no new cases and deaths in a country (2023-07-02)
# USA didn't submit new cases since 2023-05-21
covid_new['date'] = pd.to_datetime(covid_new['date'])
covid_new = covid_new[covid_new['date'] < '2023-05-20']

In [8]:
# understandig missing datas:
nan_columns = covid_new.columns[covid_new.isna().any()].tolist()
nan_columns

['continent',
 'total_cases',
 'new_cases',
 'total_deaths',
 'new_deaths',
 'reproduction_rate',
 'icu_patients',
 'hosp_patients',
 'weekly_icu_admissions',
 'weekly_hosp_admissions',
 'total_tests',
 'new_tests',
 'positive_rate',
 'tests_per_case',
 'tests_units',
 'total_vaccinations',
 'people_vaccinated',
 'people_fully_vaccinated',
 'total_boosters',
 'new_vaccinations',
 'new_people_vaccinated_smoothed',
 'stringency_index',
 'population_density',
 'median_age',
 'aged_65_older',
 'aged_70_older',
 'gdp_per_capita',
 'extreme_poverty',
 'cardiovasc_death_rate',
 'diabetes_prevalence',
 'female_smokers',
 'male_smokers',
 'handwashing_facilities',
 'hospital_beds_per_thousand',
 'life_expectancy',
 'human_development_index',
 'excess_mortality_cumulative_absolute',
 'excess_mortality_cumulative',
 'excess_mortality']

now we are going to understand each column missing data and handle it:

In [9]:
# There are a lot of missing data for countries: England, Hong Kong, Macao, Northern Cyprus, Northern Ireland, Scotland, Taiwan, Wales
missing_data_locations = ['England', 'Hong Kong', 'Macao', 'Northern Cyprus', 'Northern Ireland', 'Scotland', 'Taiwan', 'Wales']
covid_new = covid_new[~covid_new['location'].isin(missing_data_locations) ]

In [10]:
# continent:
covid_new[covid_new['continent'].isna()]

iso_code continent location       date  total_cases  new_cases  \
1506    OWID_AFR       NaN   Africa 2020-01-05          NaN        0.0   
1507    OWID_AFR       NaN   Africa 2020-01-06          NaN        0.0   
1508    OWID_AFR       NaN   Africa 2020-01-07          NaN        0.0   
1509    OWID_AFR       NaN   Africa 2020-01-08          NaN        0.0   
1510    OWID_AFR       NaN   Africa 2020-01-09          NaN        0.0   
...          ...       ...      ...        ...          ...        ...   
375788  OWID_WRL       NaN    World 2023-05-15  765587065.0        0.0   
375789  OWID_WRL       NaN    World 2023-05-16  765587065.0        0.0   
375790  OWID_WRL       NaN    World 2023-05-17  765587065.0        0.0   
375791  OWID_WRL       NaN    World 2023-05-18  765587065.0        0.0   
375792  OWID_WRL       NaN    World 2023-05-19  765587065.0        0.0   

        total_deaths  new_deaths  reproduction_rate  icu_patients  ...  \
1506             NaN         0.0                NaN           NaN  ...   
1507             NaN         0.0                NaN           NaN  ...   
1508             NaN         0.0                NaN           NaN  ...   
1509             NaN         0.0                NaN           NaN  ...   
1510             NaN         0.0                NaN           NaN  ...   
...              ...         ...                ...           ...  ...   
375788     6937640.0         0.0                NaN           NaN  ...   
375789     6937640.0         0.0                NaN           NaN  ...   
375790     6937640.0         0.0                NaN           NaN  ...   
375791     6937640.0         0.0                NaN           NaN  ...   
375792     6937640.0         0.0                NaN           NaN  ...   

        female_smokers  male_smokers  handwashing_facilities  \
1506               NaN           NaN                     NaN   
1507               NaN           NaN                     NaN   
1508               NaN           NaN                     NaN   
1509               NaN           NaN                     NaN   
1510               NaN           NaN                     NaN   
...                ...           ...                     ...   
375788           6.434        34.635                   60.13   
375789           6.434        34.635                   60.13   
375790           6.434        34.635                   60.13   
375791           6.434        34.635                   60.13   
375792           6.434        34.635                   60.13   

        hospital_beds_per_thousand  life_expectancy  human_development_index  \
1506                           NaN              NaN                      NaN   
1507                           NaN              NaN                      NaN   
1508                           NaN              NaN                      NaN   
1509                           NaN              NaN                      NaN   
1510                           NaN              NaN                      NaN   
...                            ...              ...                      ...   
375788                       2.705            72.58                    0.737   
375789                       2.705            72.58                    0.737   
375790                       2.705            72.58                    0.737   
375791                       2.705            72.58                    0.737   
375792                       2.705            72.58                    0.737   

          population excess_mortality_cumulative_absolute  \
1506    1.426737e+09                                  NaN   
1507    1.426737e+09                                  NaN   
1508    1.426737e+09                                  NaN   
1509    1.426737e+09                                  NaN   
1510    1.426737e+09                                  NaN   
...              ...                                  ...   
375788  7.975105e+09                                  NaN   
375789  7.97

<div dir=rtl >
<font  size=3>
در اینجا متوجه می‌شویم که اون‌هایی که ستون قاره مربوطه نال است، نام قاره در ستون مکان آمده است، حال اول چک کنیم که تعداد مبتلا‌های کشور‌های با خود قاره برابر است یا نه.
</font>
</div>

In [11]:
africa_datas = covid_new[covid_new['continent'] == 'Africa']
africa_continent_datas = covid_new[covid_new['location'] == 'Africa']
africa_datas[africa_datas['date'] == '2024-02-18']['total_cases'].sum() == africa_continent_datas[africa_continent_datas['date'] == '2024-02-18']['total_cases']

Series([], Name: total_cases, dtype: bool)

<div dir=rtl >
<font  size=3>
متوجه می‌شویم که داده‌هایی که ستون قاره آن ها خالی است تنها آمده است کشورها را جمع زده است. پس سطر‌های مربوط را پاک می‌کنیم.
</font>
</div>

In [12]:
covid_new = covid_new.drop(covid_new[covid_new['continent'].isna()].index, axis=0)

In [13]:
covid_new[covid_new['continent'].isna()].count

<bound method DataFrame.count of Empty DataFrame
Columns: [iso_code, continent, location, date, total_cases, new_cases, total_deaths, new_deaths, reproduction_rate, icu_patients, hosp_patients, weekly_icu_admissions, weekly_hosp_admissions, total_tests, new_tests, positive_rate, tests_per_case, tests_units, total_vaccinations, people_vaccinated, people_fully_vaccinated, total_boosters, new_vaccinations, new_people_vaccinated_smoothed, stringency_index, population_density, median_age, aged_65_older, aged_70_older, gdp_per_capita, extreme_poverty, cardiovasc_death_rate, diabetes_prevalence, female_smokers, male_smokers, handwashing_facilities, hospital_beds_per_thousand, life_expectancy, human_development_index, population, excess_mortality_cumulative_absolute, excess_mortality_cumulative, excess_mortality]
Index: []

[0 rows x 43 columns]>

In [14]:
# total_cases
covid_new[covid_new['total_cases'].isna()]

iso_code continent     location       date  total_cases  new_cases  \
0           AFG      Asia  Afghanistan 2020-01-05          NaN        0.0   
1           AFG      Asia  Afghanistan 2020-01-06          NaN        0.0   
2           AFG      Asia  Afghanistan 2020-01-07          NaN        0.0   
3           AFG      Asia  Afghanistan 2020-01-08          NaN        0.0   
4           AFG      Asia  Afghanistan 2020-01-09          NaN        0.0   
...         ...       ...          ...        ...          ...        ...   
379176      ZWE    Africa     Zimbabwe 2020-03-17          NaN        0.0   
379177      ZWE    Africa     Zimbabwe 2020-03-18          NaN        0.0   
379178      ZWE    Africa     Zimbabwe 2020-03-19          NaN        0.0   
379179      ZWE    Africa     Zimbabwe 2020-03-20          NaN        0.0   
379180      ZWE    Africa     Zimbabwe 2020-03-21          NaN        0.0   

        total_deaths  new_deaths  reproduction_rate  icu_patients  ...  \
0                NaN         0.0                NaN           NaN  ...   
1                NaN         0.0                NaN           NaN  ...   
2                NaN         0.0                NaN           NaN  ...   
3                NaN         0.0                NaN           NaN  ...   
4                NaN         0.0                NaN           NaN  ...   
...              ...         ...                ...           ...  ...   
379176           5.0         0.0                NaN           NaN  ...   
379177           5.0         0.0                NaN           NaN  ...   
379178           5.0         0.0                NaN           NaN  ...   
379179           5.0         0.0                NaN           NaN  ...   
379180           5.0         0.0                NaN           NaN  ...   

        female_smokers  male_smokers  handwashing_facilities  \
0                  NaN           NaN                  37.746   
1                  NaN           NaN                  37.746   
2                  NaN           NaN                  37.746   
3                  NaN           NaN                  37.746   
4                  NaN           NaN                  37.746   
...                ...           ...                     ...   
379176             1.6          30.7                  36.791   
379177             1.6          30.7                  36.791   
379178             1.6          30.7                  36.791   
379179             1.6          30.7                  36.791   
379180             1.6          30.7                  36.791   

        hospital_beds_per_thousand  life_expectancy  human_development_index  \
0                              0.5            64.83                    0.511   
1                              0.5            64.83                    0.511   
2                              0.5            64.83                    0.511   
3                              0.5            64.83                    0.511   
4                              0.5            64.83                    0.511   
...                            ...              ...                      ...   
379176                         1.7            61.49                    0.571   
379177                         1.7            61.49                    0.571   
379178                         1.7            61.49                    0.571   
379179                         1.7            61.49                    0.571   
379180                         1.7            61.49                    0.571   

        population excess_mortality_cumulative_absolute  \
0       41128772.0                                  NaN   
1       41128772.0                                  NaN   
2       41128772.0                                  NaN   
3       41128772.0                                  NaN   
4       41128772.0                                  NaN   
...            ...                                  ...   
379176  16320539.0                                

In [15]:
# we can see that when there is no cases the total_cases is NaN so we replace the NaN with 0:
covid_new['total_cases'] = covid_new['total_cases'].fillna(0)

In [16]:
covid_new[covid_new['total_cases'].isna()]

Empty DataFrame
Columns: [iso_code, continent, location, date, total_cases, new_cases, total_deaths, new_deaths, reproduction_rate, icu_patients, hosp_patients, weekly_icu_admissions, weekly_hosp_admissions, total_tests, new_tests, positive_rate, tests_per_case, tests_units, total_vaccinations, people_vaccinated, people_fully_vaccinated, total_boosters, new_vaccinations, new_people_vaccinated_smoothed, stringency_index, population_density, median_age, aged_65_older, aged_70_older, gdp_per_capita, extreme_poverty, cardiovasc_death_rate, diabetes_prevalence, female_smokers, male_smokers, handwashing_facilities, hospital_beds_per_thousand, life_expectancy, human_development_index, population, excess_mortality_cumulative_absolute, excess_mortality_cumulative, excess_mortality]
Index: []

[0 rows x 43 columns]

In [17]:
# new_cases
covid_new[covid_new['new_cases'].isna()]

iso_code      continent                      location       date  \
13554       ARG  South America                     Argentina 2020-01-01   
13555       ARG  South America                     Argentina 2020-01-02   
13556       ARG  South America                     Argentina 2020-01-03   
13557       ARG  South America                     Argentina 2020-01-04   
34033       BLZ  North America                        Belize 2022-04-10   
92277       ECU  South America                       Ecuador 2020-09-13   
98707       GNQ         Africa             Equatorial Guinea 2022-03-20   
135722      GTM  North America                     Guatemala 2020-04-05   
199308      MWI         Africa                        Malawi 2022-11-06   
201392      MDV           Asia                      Maldives 2020-03-29   
209995      MRT         Africa                    Mauritania 2023-02-12   
212377      MYT         Africa                       Mayotte 2021-05-23   
213379      MEX  North America                        Mexico 2020-01-01   
213380      MEX  North America                        Mexico 2020-01-02   
213381      MEX  North America                        Mexico 2020-01-03   
213382      MEX  North America                        Mexico 2020-01-04   
307344      SXM  North America     Sint Maarten (Dutch part) 2020-06-07   
335670      THA           Asia                      Thailand 2020-01-04   
335692      THA           Asia                      Thailand 2020-01-26   
360065      VIR  North America  United States Virgin Islands 2020-10-11   
374561      ESH         Africa                Western Sahara 2022-04-20   

        total_cases  new_cases  total_deaths  new_deaths  reproduction_rate  \
13554           0.0        NaN           NaN         NaN                NaN   
13555           0.0        NaN           NaN         NaN                NaN   
13556           0.0        NaN           NaN         NaN                NaN   
13557           0.0        NaN           NaN         NaN                NaN   
34033       57287.0        NaN         664.0         8.0               0.75   
92277      116451.0        NaN       10864.0      4140.0               1.06   
98707       15800.0        NaN         183.0         0.0               0.40   
135722         50.0        NaN           1.0         0.0                NaN   
199308      88009.0        NaN        2685.0         2.0               0.12   
201392         16.0        NaN           NaN         0.0                NaN   
209995      63438.0        NaN         997.0         0.0                NaN   
212377      19301.0        NaN         171.0         0.0                NaN   
213379          0.0        NaN           NaN         NaN                NaN   
213380          0.0        NaN           NaN         NaN                NaN   
213381          0.0        NaN           NaN         NaN                NaN   
213382          0.0        NaN           NaN         NaN                NaN   
307344         77.0        NaN          15.0         0.0                NaN   
335670          0.0        NaN           NaN         NaN                NaN   
335692          5.0        NaN           NaN         0.0                NaN   
360065       1324.0        NaN          20.0         0.0                NaN   
374561          0.0        NaN           NaN         NaN                NaN   

        icu_patients  ...  female_smokers  male_smokers  \
13554            NaN  ...            16.2          27.7   
13555            NaN  ...            16.2          27.7   
13556            NaN  ...            16.2          27.7   
13557            NaN  ...            16.2          27.7   
34033            NaN  ...             NaN           NaN   
92277            NaN  ...             2.0          12.3   
98707            NaN  ...             NaN           NaN   
135722           NaN  ...             NaN           NaN   
199308           NaN  ...             4.4          24.7   
201392           NaN  ...  

In [18]:
# It seems that these remaining NaN data for new cases are 0 at the beginning of the pandemic
covid_new['new_cases'] = covid_new['new_cases'].fillna(0)

In [26]:
# making sure that we have problem in total_cases for new_cases we filled.
for country_name in covid_new['location'].unique():
    index_values = covid_new[(covid_new['new_cases'] == 0) & (covid_new['location'] == country_name)]['total_cases']
    index_zero = covid_new[(covid_new['new_cases'] == 0) & (covid_new['location'] == country_name)].index
    if not index_zero.empty:
        index_zero = index_zero.tolist()
        index_zero.pop()
        next_index = [i + 1 for i in index_zero]
        next_cases_value = covid_new.loc[next_index, 'total_cases']
        difference = next_cases_value - index_values
        difference = difference.tolist()
        print(f'{country_name} : {list(filter(lambda x: x != 0 and x is not None and not math.isnan(x), difference))}')
    else:
        print(f'{country_name} : No index with zero new cases found')

Afghanistan : []
Albania : []
Algeria : []
American Samoa : []
Andorra : []
Angola : []
Anguilla : []
Antigua and Barbuda : []
Argentina : []
Armenia : []
Aruba : []
Australia : []
Austria : []
Azerbaijan : []
Bahamas : []
Bahrain : []
Bangladesh : []
Barbados : []
Belarus : []
Belgium : []
Belize : []
Benin : []
Bermuda : []
Bhutan : []
Bolivia : []
Bonaire Sint Eustatius and Saba : []
Bosnia and Herzegovina : []
Botswana : []
Brazil : []
British Virgin Islands : []
Brunei : []
Bulgaria : []
Burkina Faso : []
Burundi : []
Cambodia : []
Cameroon : []
Canada : []
Cape Verde : []
Cayman Islands : []
Central African Republic : []
Chad : []
Chile : []
China : []
Colombia : []
Comoros : []
Congo : []
Cook Islands : []
Costa Rica : []
Cote d'Ivoire : []
Croatia : []
Cuba : []
Curacao : []
Cyprus : []
Czechia : []
Democratic Republic of Congo : []
Denmark : []
Djibouti : []
Dominica : []
Dominican Republic : []
Ecuador : []
Egypt : []
El Salvador : []
Equatorial Guinea : []
Eritrea : []
Eston

In [27]:
# total_deaths
covid_new[covid_new['total_deaths'].isna()]

iso_code continent     location       date  total_cases  new_cases  \
0           AFG      Asia  Afghanistan 2020-01-05          0.0        0.0   
1           AFG      Asia  Afghanistan 2020-01-06          0.0        0.0   
2           AFG      Asia  Afghanistan 2020-01-07          0.0        0.0   
3           AFG      Asia  Afghanistan 2020-01-08          0.0        0.0   
4           AFG      Asia  Afghanistan 2020-01-09          0.0        0.0   
...         ...       ...          ...        ...          ...        ...   
379162      ZWE    Africa     Zimbabwe 2020-03-03          0.0        0.0   
379163      ZWE    Africa     Zimbabwe 2020-03-04          0.0        0.0   
379164      ZWE    Africa     Zimbabwe 2020-03-05          0.0        0.0   
379165      ZWE    Africa     Zimbabwe 2020-03-06          0.0        0.0   
379166      ZWE    Africa     Zimbabwe 2020-03-07          0.0        0.0   

        total_deaths  new_deaths  reproduction_rate  icu_patients  ...  \
0                NaN         0.0                NaN           NaN  ...   
1                NaN         0.0                NaN           NaN  ...   
2                NaN         0.0                NaN           NaN  ...   
3                NaN         0.0                NaN           NaN  ...   
4                NaN         0.0                NaN           NaN  ...   
...              ...         ...                ...           ...  ...   
379162           NaN         0.0                NaN           NaN  ...   
379163           NaN         0.0                NaN           NaN  ...   
379164           NaN         0.0                NaN           NaN  ...   
379165           NaN         0.0                NaN           NaN  ...   
379166           NaN         0.0                NaN           NaN  ...   

        female_smokers  male_smokers  handwashing_facilities  \
0                  NaN           NaN                  37.746   
1                  NaN           NaN                  37.746   
2                  NaN           NaN                  37.746   
3                  NaN           NaN                  37.746   
4                  NaN           NaN                  37.746   
...                ...           ...                     ...   
379162             1.6          30.7                  36.791   
379163             1.6          30.7                  36.791   
379164             1.6          30.7                  36.791   
379165             1.6          30.7                  36.791   
379166             1.6          30.7                  36.791   

        hospital_beds_per_thousand  life_expectancy  human_development_index  \
0                              0.5            64.83                    0.511   
1                              0.5            64.83                    0.511   
2                              0.5            64.83                    0.511   
3                              0.5            64.83                    0.511   
4                              0.5            64.83                    0.511   
...                            ...              ...                      ...   
379162                         1.7            61.49                    0.571   
379163                         1.7            61.49                    0.571   
379164                         1.7            61.49                    0.571   
379165                         1.7            61.49                    0.571   
379166                         1.7            61.49                    0.571   

        population excess_mortality_cumulative_absolute  \
0       41128772.0                                  NaN   
1       41128772.0                                  NaN   
2       41128772.0                                  NaN   
3       41128772.0                                  NaN   
4       41128772.0                                  NaN   
...            ...                                  ...   
379162  16320539.0                                

In [28]:
covid_new['total_deaths'] = covid_new['total_deaths'].fillna(0)

In [29]:
covid_new[covid_new['total_cases'].isna()]

Empty DataFrame
Columns: [iso_code, continent, location, date, total_cases, new_cases, total_deaths, new_deaths, reproduction_rate, icu_patients, hosp_patients, weekly_icu_admissions, weekly_hosp_admissions, total_tests, new_tests, positive_rate, tests_per_case, tests_units, total_vaccinations, people_vaccinated, people_fully_vaccinated, total_boosters, new_vaccinations, new_people_vaccinated_smoothed, stringency_index, population_density, median_age, aged_65_older, aged_70_older, gdp_per_capita, extreme_poverty, cardiovasc_death_rate, diabetes_prevalence, female_smokers, male_smokers, handwashing_facilities, hospital_beds_per_thousand, life_expectancy, human_development_index, population, excess_mortality_cumulative_absolute, excess_mortality_cumulative, excess_mortality]
Index: []

[0 rows x 43 columns]

In [30]:
# new_deaths
covid_new[covid_new['new_deaths'].isna()]

iso_code      continent                         location       date  \
13554       ARG  South America                        Argentina 2020-01-01   
13555       ARG  South America                        Argentina 2020-01-02   
13556       ARG  South America                        Argentina 2020-01-03   
13557       ARG  South America                        Argentina 2020-01-04   
41388       BES  North America  Bonaire Sint Eustatius and Saba 2021-10-17   
58223       CAN  North America                           Canada 2022-06-19   
66057       CHL  South America                            Chile 2023-04-02   
132920      GLP  North America                       Guadeloupe 2020-11-01   
213379      MEX  North America                           Mexico 2020-01-01   
213380      MEX  North America                           Mexico 2020-01-02   
213381      MEX  North America                           Mexico 2020-01-03   
213382      MEX  North America                           Mexico 2020-01-04   
261923      PAN  North America                           Panama 2023-05-07   
276003      REU         Africa                          Reunion 2020-08-30   
305067      SLE         Africa                     Sierra Leone 2022-06-12   
335670      THA           Asia                         Thailand 2020-01-04   
335993      THA           Asia                         Thailand 2020-11-22   
374561      ESH         Africa                   Western Sahara 2022-04-20   

        total_cases  new_cases  total_deaths  new_deaths  reproduction_rate  \
13554           0.0        0.0           0.0         NaN                NaN   
13555           0.0        0.0           0.0         NaN                NaN   
13556           0.0        0.0           0.0         NaN                NaN   
13557           0.0        0.0           0.0         NaN                NaN   
41388        2306.0      102.0          19.0         NaN                NaN   
58223     3915721.0    23312.0       41017.0         NaN               1.01   
66057     5264330.0    14253.0       61050.0         NaN                NaN   
132920       7742.0      268.0         126.0         NaN                NaN   
213379          0.0        0.0           0.0         NaN                NaN   
213380          0.0        0.0           0.0         NaN                NaN   
213381          0.0        0.0           0.0         NaN                NaN   
213382          0.0        0.0           0.0         NaN                NaN   
261923    1037324.0      591.0        8620.0         NaN                NaN   
276003       1557.0      440.0           3.0         NaN                NaN   
305067       7682.0        0.0         125.0         NaN               0.41   
335670          0.0        0.0           0.0         NaN                NaN   
335993       3913.0       39.0           0.0         NaN               1.22   
374561          0.0        0.0           0.0         NaN                NaN   

        icu_patients  ...  female_smokers  male_smokers  \
13554            NaN  ...            16.2          27.7   
13555            NaN  ...            16.2          27.7   
13556            NaN  ...            16.2          27.7   
13557            NaN  ...            16.2          27.7   
41388            NaN  ...             NaN           NaN   
58223          166.0  ...            12.0          16.6   
66057           73.0  ...            34.2          41.5   
132920           NaN  ...             NaN           NaN   
213379           NaN  ...             6.9          21.4   
213380           NaN  ...             6.9          21.4   
213381           NaN  ...             6.9          21.4   
213382           NaN  ...             6.9          21.4   
261923           NaN  ...             2.4           9.9   
276003           NaN  ...             NaN           NaN   
305067           NaN  ...             8.8          41.3   
335670           NaN  ...             1.9          38.8   
335993           Na

In [32]:
# It seems that these remaining NaN data for new death are 0 at the beginning of the pandemic
covid_new['new_deaths'] = covid_new['new_deaths'].fillna(0)

In [34]:
# making sure that we have problem in total_deaths for new_deaths we filled.
for country_name in covid_new['location'].unique():
    index_values = covid_new[(covid_new['new_deaths'] == 0) & (covid_new['location'] == country_name)]['total_deaths']
    index_zero = covid_new[(covid_new['new_deaths'] == 0) & (covid_new['location'] == country_name)].index
    if not index_zero.empty:
        index_zero = index_zero.tolist()
        index_zero.pop()
        next_index = [i + 1 for i in index_zero]
        next_cases_value = covid_new.loc[next_index, 'total_deaths']
        difference = next_cases_value - index_values
        difference = difference.tolist()
        print(f'{country_name} : {list(filter(lambda x: x != 0 and x is not None and not math.isnan(x), difference))}')
    else:
        print(f'{country_name} : No index with zero new cases found')

Afghanistan : []
Albania : []
Algeria : []
American Samoa : []
Andorra : []
Angola : []
Anguilla : []
Antigua and Barbuda : []
Argentina : []
Armenia : []
Aruba : []
Australia : []
Austria : []
Azerbaijan : []
Bahamas : []
Bahrain : []
Bangladesh : []
Barbados : []
Belarus : []
Belgium : []
Belize : []
Benin : []
Bermuda : []
Bhutan : []
Bolivia : []
Bonaire Sint Eustatius and Saba : []
Bosnia and Herzegovina : []
Botswana : []
Brazil : []
British Virgin Islands : []
Brunei : []
Bulgaria : []
Burkina Faso : []
Burundi : []
Cambodia : []
Cameroon : []
Canada : []
Cape Verde : []
Cayman Islands : []
Central African Republic : []
Chad : []
Chile : []
China : []
Colombia : []
Comoros : []
Congo : []
Cook Islands : []
Costa Rica : []
Cote d'Ivoire : []
Croatia : []
Cuba : []
Curacao : []
Cyprus : []
Czechia : []
Democratic Republic of Congo : []
Denmark : []
Djibouti : []
Dominica : []
Dominican Republic : []
Ecuador : []
Egypt : []
El Salvador : []
Equatorial Guinea : []
Eritrea : []
Eston

In [42]:
# reproduction_rate
covid_new['reproduction_rate'].isna().sum()/len(covid_new['reproduction_rate'])

0.3656930404354588

In [49]:
len(covid_new['location'].unique())

235

In [62]:
# As we can see about 37 percent of data's missing, so we have to choose how we can fill the null cells
# First we plot box plot for each country:

import matplotlib.pyplot as plt
import seaborn as sns

# Set seaborn style
sns.set(style="whitegrid")

# Create subplots
fig, axs = plt.subplots(47, 5, figsize=(15, 200), sharex=True, sharey=True)

# Flatten the axs array to iterate over them easily
axs = axs.flatten()

# Iterate over each country name and corresponding axis
for i, country_name in enumerate(covid_new['location'].unique()):
    print(f"{country_name} : {country_data['reproduction_rate'].isna().sum()/len(country_data)}")
    country_data = covid_new[covid_new['location'] == country_name]
    sns.boxplot(y=country_data['reproduction_rate'].dropna(), ax=axs[i])
    axs[i].set_title(f'Reproduction Rate: {country_name}', fontsize=10)
    axs[i].tick_params(axis='x', labelrotation=45)
    axs[i].set_xlabel('')
    axs[i].set_ylabel('')

# Remove extra subplots
for j in range(len(covid_new['location'].unique()), len(axs)):
    fig.delaxes(axs[j])

plt.tight_layout()
plt.show()


<IPython.core.display.Javascript object>

Afghanistan : 0.2282696994313566
Albania : 0.17952883834281072
Algeria : 0.17546709991876522
American Samoa : 0.17384240454914704
Andorra : 1.0
Angola : 0.17465475223395613
Anguilla : 0.239642567018684
Antigua and Barbuda : 1.0
Argentina : 0.3281884646628757
Armenia : 0.1757085020242915
Aruba : 0.17221770917952883
Australia : 1.0
Austria : 0.16490658001624695
Azerbaijan : 0.16490658001624695
Bahamas : 0.17790414297319251
Bahrain : 0.22502030869212022
Bangladesh : 0.16490658001624695
Barbados : 0.1868399675060926
Belarus : 0.264825345247766
Belgium : 0.18115353371242893
Belize : 0.16165718927701056
Benin : 0.2859463850528026
Bermuda : 0.21202274573517466
Bhutan : 1.0
Bolivia : 0.2802599512591389
Bonaire Sint Eustatius and Saba : 0.18196588139723802
Bosnia and Herzegovina : 1.0
Botswana : 0.17465475223395613
Brazil : 0.2550771730300569
British Virgin Islands : 0.16734362307067424
Brunei : 1.0
Bulgaria : 0.17627944760357434
Burkina Faso : 0.17303005686433795
Burundi : 0.17627944760357434


iso_code continent location       date  total_cases  new_cases  \
155242      IRN      Asia     Iran 2020-01-05          0.0        0.0   
155243      IRN      Asia     Iran 2020-01-06          0.0        0.0   
155244      IRN      Asia     Iran 2020-01-07          0.0        0.0   
155245      IRN      Asia     Iran 2020-01-08          0.0        0.0   
155246      IRN      Asia     Iran 2020-01-09          0.0        0.0   
...         ...       ...      ...        ...          ...        ...   
156468      IRN      Asia     Iran 2023-05-15    7610676.0        0.0   
156469      IRN      Asia     Iran 2023-05-16    7610676.0        0.0   
156470      IRN      Asia     Iran 2023-05-17    7610676.0        0.0   
156471      IRN      Asia     Iran 2023-05-18    7610676.0        0.0   
156472      IRN      Asia     Iran 2023-05-19    7610676.0        0.0   

        total_deaths  new_deaths  reproduction_rate  icu_patients  ...  \
155242           0.0         0.0                NaN           NaN  ...   
155243           0.0         0.0                NaN           NaN  ...   
155244           0.0         0.0                NaN           NaN  ...   
155245           0.0         0.0                NaN           NaN  ...   
155246           0.0         0.0                NaN           NaN  ...   
...              ...         ...                ...           ...  ...   
156468      146204.0         0.0                NaN           NaN  ...   
156469      146204.0         0.0                NaN           NaN  ...   
156470      146204.0         0.0                NaN           NaN  ...   
156471      146204.0         0.0                NaN           NaN  ...   
156472      146204.0         0.0                NaN           NaN  ...   

        female_smokers  male_smokers  handwashing_facilities  \
155242             0.8          21.1                     NaN   
155243             0.8          21.1                     NaN   
155244             0.8          21.1                     NaN   
155245             0.8          21.1                     NaN   
155246             0.8          21.1                     NaN   
...                ...           ...                     ...   
156468             0.8          21.1                     NaN   
156469             0.8          21.1                     NaN   
156470             0.8          21.1                     NaN   
156471             0.8          21.1                     NaN   
156472             0.8          21.1                     NaN   

        hospital_beds_per_thousand  life_expectancy  human_development_index  \
155242                         1.5            76.68                    0.783   
155243                         1.5            76.68                    0.783   
155244                         1.5            76.68                    0.783   
155245                         1.5            76.68                    0.783   
155246                         1.5            76.68                    0.783   
...                            ...              ...                      ...   
156468                         1.5            76.68                    0.783   
156469                         1.5            76.68                    0.783   
156470                         1.5            76.68                    0.783   
156471                         1.5            76.68                    0.783   
156472                         1.5            76.68                    0.783   

        population excess_mortality_cumulative_absolute  \
155242  88550568.0                               -531.5   
155243  88550568.0                                  NaN   
155244  88550568.0                                  NaN   
155245  88550568.0                                  NaN   
155246  88550568.0                                  NaN   
...            ...                                  ...   
156468  88550568.0                                  NaN   
156469  88550568.0                     